## Financial Services

In [1]:
from langchain.text_splitter import CharacterTextSplitter
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.docstore.document import Document
from langchain.document_loaders import UnstructuredURLLoader
from langchain.chains.qa_with_sources import load_qa_with_sources_chain
from langchain.vectorstores.pinecone import Pinecone
from langchain.chains import RetrievalQA
from langchain import OpenAI
from langchain_openai import ChatOpenAI
from cleantext import clean
import os
import nltk
import pinecone
import openai
import dotenv

Since the GPL-licensed package `unidecode` is not installed, using Python's `unicodedata` package which yields worse results.


#### Wikipedia

In [2]:
from langchain_community.document_loaders import WikipediaLoader

In [65]:
docs = WikipediaLoader(query="International Financial Services Centres Authority", doc_content_chars_max = 100000, load_max_docs=1).load()

In [66]:
docs[0].metadata  # meta-information of the Document

{'title': 'International Financial Services Centres Authority',
 'summary': 'The International Financial Services Centres Authority (IFSCA) is the regulatory body for the Indian special economic zones such as the GIFT International Financial Services Centre for International Financial Services and commodity markets under the ownership of the Government of India. It was established in 2020, under the International Financial Services Centres Authority Act, 2019. The International Financial Services Centre (IFSC) is located in Gujarat International Finance Tec-City (GIFT City).\n\nIn December 2015 the first International Financial Services Centre (IFSC) in India was set up in Gujarat International Finance Tec-City (GIFT City).\nIn 2019 the Government of India enacted an Act of Parliament called the International Financial Services Centres Authority Act, 2019. \n\nOn April 27, 2020, The IFSCA was established as a statutory body under the International Financial Services Centres Authority A

In [67]:
print(docs[0].page_content)

The International Financial Services Centres Authority (IFSCA) is the regulatory body for the Indian special economic zones such as the GIFT International Financial Services Centre for International Financial Services and commodity markets under the ownership of the Government of India. It was established in 2020, under the International Financial Services Centres Authority Act, 2019. The International Financial Services Centre (IFSC) is located in Gujarat International Finance Tec-City (GIFT City).

In December 2015 the first International Financial Services Centre (IFSC) in India was set up in Gujarat International Finance Tec-City (GIFT City).
In 2019 the Government of India enacted an Act of Parliament called the International Financial Services Centres Authority Act, 2019. 

On April 27, 2020, The IFSCA was established as a statutory body under the International Financial Services Centres Authority Act, 2019. On April 27, 2020, inauguration of the IFSCA by the Finance Minister of 

In [68]:
# documents = []
documents.extend(docs)

In [69]:
len(documents)

3

In [70]:
documents

[Document(metadata={'title': 'Real Estate (Regulation and Development) Act, 2016', 'summary': 'The Real Estate (Regulation and Development) Act, 2016 is an Act of the Parliament of India which seeks to protect home-buyers as well as help boost investments in the real estate industry. The Act establishes a Real Estate Regulatory Authority (RERA) in each state for regulation of the real estate sector and also acts as an adjudicating body for speedy dispute resolution. The bill was passed by the Rajya Sabha on 10 March 2016 and by the Lok Sabha on 15 March 2016. The Act came into force on 1 May 2016 with 61 of 92 sections notified. The remaining provisions came into force on 1 May 2017. The Central and state governments are liable to notify the Rules under the Act within a statutory period of six months.\n\nThe Real Estate Regulatory Authority (RERA) Bill was introduced in 2013. In December 2015, the Union Cabinet of India had approved 20 major amendments to the bill based on the recommen

In [71]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
texts = text_splitter.split_documents(documents)
texts

[Document(metadata={'title': 'Real Estate (Regulation and Development) Act, 2016', 'summary': 'The Real Estate (Regulation and Development) Act, 2016 is an Act of the Parliament of India which seeks to protect home-buyers as well as help boost investments in the real estate industry. The Act establishes a Real Estate Regulatory Authority (RERA) in each state for regulation of the real estate sector and also acts as an adjudicating body for speedy dispute resolution. The bill was passed by the Rajya Sabha on 10 March 2016 and by the Lok Sabha on 15 March 2016. The Act came into force on 1 May 2016 with 61 of 92 sections notified. The remaining provisions came into force on 1 May 2017. The Central and state governments are liable to notify the Rules under the Act within a statutory period of six months.\n\nThe Real Estate Regulatory Authority (RERA) Bill was introduced in 2013. In December 2015, the Union Cabinet of India had approved 20 major amendments to the bill based on the recommen

In [10]:
dotenv.load_dotenv()

True

In [9]:
%cd regulatory_compliance_advisor

/teamspace/studios/this_studio/regulatory_compliance_advisor


/home/zeus/miniconda3/envs/cloudspace/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: using dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [10]:
!pwd

/teamspace/studios/this_studio


In [11]:
os.environ["OPENAI_API_KEY"] = os.getenv("OPENAI_API_KEY")

In [12]:

#Set the pinecone key
from pinecone import Pinecone
#os.environ["PINECONE_API_KEY"] = os.getenv("PINECONE_API_KEY")

api_key = os.getenv("PINECONE_API_KEY")

# configure client
pc = Pinecone(api_key=api_key)

In [21]:
from pinecone import ServerlessSpec

cloud = 'aws'
region = 'us-east-1'

spec = ServerlessSpec(cloud=cloud, region=region)

In [3]:
import time
index_name = "finance"

In [23]:
# if index_name in pc.list_indexes().names():
#     pc.delete_index(index_name)

In [24]:
# we create a new index
pc.create_index(
        index_name,
        dimension=1536,  # dimensionality of text-embedding-ada-002
        metric='dotproduct',
        spec=spec
    )

In [25]:
# wait for index to be initialized
while not pc.describe_index(index_name).status['ready']:
    time.sleep(1)

In [52]:
index = pc.Index(index_name)
index.describe_index_stats()

{'dimension': 1536,
 'index_fullness': 0.0,
 'namespaces': {'': {'vector_count': 1643}},
 'total_vector_count': 1643}

In [13]:
from langchain_pinecone import PineconeVectorStore
from langchain_openai import OpenAIEmbeddings

embeddings = OpenAIEmbeddings()
vectorstore = PineconeVectorStore(index_name=index_name, embedding=embeddings)

In [72]:
vectorstore_from_docs = PineconeVectorStore.from_documents(
        texts,
        index_name=index_name,
        embedding=embeddings
    )

In [19]:
query = "Financial regualtion in China."
vectorstore.similarity_search(query)

[Document(metadata={'source': 'https://en.wikipedia.org/wiki/Financial_regulation_in_India', 'summary': 'Financial regulation in India is governed by a number of regulatory bodies. Financial regulation is a form of regulation or supervision, which subjects financial institutions to certain requirements, restrictions and guidelines, aiming to maintain the stability and integrity of the financial system. This may be handled by either a government or non-government organization. Financial regulation has also influenced the structure of banking sectors by increasing the variety of financial products available. Financial regulation forms one of three legal categories which constitutes the content of financial law, the other two being market practices and case law.', 'title': 'Financial regulation in India'}, page_content='Financial regulation in India is governed by a number of regulatory bodies. Financial regulation is a form of regulation or supervision, which subjects financial instituti

## LLM result

In [20]:
from langchain_openai import ChatOpenAI
from langchain.chains import RetrievalQA
# completion llm
llm = ChatOpenAI(
    openai_api_key=os.getenv("OPENAI_API_KEY"),
    model_name='gpt-4o-mini',
    temperature=0.0
)
qa = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",
    retriever=vectorstore.as_retriever()
)
qa.run(query)

"I don't know."

#### URL

In [48]:
#n_weblinks = int(input("How many web links you want the RAG agent to refer for response generation & insights? Enter here: "))
urls = []
inp = input("Enter Link:")
urls.append(inp)
print("URL:", urls)

URL: ['https://finance.ec.europa.eu/financial-crime/anti-money-laundering-and-countering-financing-terrorism-eu-level_en#legislation']


In [49]:
loader = UnstructuredURLLoader(urls=urls, show_progress_bar=True)
urls = loader.load()

100%|██████████| 1/1 [00:00<00:00,  1.65it/s]


In [50]:
# documents = []
documents.extend(urls)

In [51]:
documents

[Document(metadata={'source': 'https://finance.ec.europa.eu/banking/insurance/insurance-distribution_en#legislation'}, page_content='Page contents\n\nEU rules on insurance distribution\n\nInsurance distribution means to sell, propose to sell, advise on or prepare in any other way the conclusion of insurance contracts. It also covers sales of insurance products through websites, including comparison websites if they allow concluding an insurance contract.\n\nThe sale of insurance products in the\xa0EU is regulated by the insurance distribution directive (IDD) adopted in\xa02016. The IDD applies to all sellers of insurance products\n\ninsurance intermediaries, such as agents and brokers, which have to be registered in their home country and meet certain minimum requirements\n\ninsurance companies that sell directly to consumers\n\nand also to so-called “ancillary insurance intermediaries”. These are businesses offering insurance as an add-on to products and services proposed by them. Typ

In [52]:
print(documents[0].page_content)

Page contents

EU rules on insurance distribution

Insurance distribution means to sell, propose to sell, advise on or prepare in any other way the conclusion of insurance contracts. It also covers sales of insurance products through websites, including comparison websites if they allow concluding an insurance contract.

The sale of insurance products in the EU is regulated by the insurance distribution directive (IDD) adopted in 2016. The IDD applies to all sellers of insurance products

insurance intermediaries, such as agents and brokers, which have to be registered in their home country and meet certain minimum requirements

insurance companies that sell directly to consumers

and also to so-called “ancillary insurance intermediaries”. These are businesses offering insurance as an add-on to products and services proposed by them. Typical examples include travel agencies or airlines offering travel insurance or sellers of electrical appliance proposing insurance against theft and da

In [53]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
texts = text_splitter.split_documents(documents)
texts

[Document(metadata={'source': 'https://finance.ec.europa.eu/banking/insurance/insurance-distribution_en#legislation'}, page_content='Page contents\n\nEU rules on insurance distribution\n\nInsurance distribution means to sell, propose to sell, advise on or prepare in any other way the conclusion of insurance contracts. It also covers sales of insurance products through websites, including comparison websites if they allow concluding an insurance contract.\n\nThe sale of insurance products in the\xa0EU is regulated by the insurance distribution directive (IDD) adopted in\xa02016. The IDD applies to all sellers of insurance products'),
 Document(metadata={'source': 'https://finance.ec.europa.eu/banking/insurance/insurance-distribution_en#legislation'}, page_content='insurance intermediaries, such as agents and brokers, which have to be registered in their home country and meet certain minimum requirements\n\ninsurance companies that sell directly to consumers'),
 Document(metadata={'sourc

In [62]:

clean_url_text = clean(text=texts,
            fix_unicode=True,
            to_ascii=True,
            lower=True,
            no_line_breaks=False,
            no_urls=False,
            no_emails=False,
            no_phone_numbers=False,
            no_numbers=False,
            no_digits=False,
            no_currency_symbols=False,
            no_punct=False,
            lang="en"
            )
clean_url_text

'[document(metadata={\'source\': \'https://eur-lex.europa.eu/legal-content/en/txt/?uri=celex:32021l0338\'}, page_content=\'skip to main content\naccess to european union law\neur-lex access to european union law\nenglish\nen\n(current language)\'), document(metadata={\'source\': \'https://eur-lex.europa.eu/legal-content/en/txt/?uri=celex:32021l0338\'}, page_content=\'language\n(bg)\nespanol (es)\ncestina (cs)\ndansk (da)\ndeutsch (de)\neesti keel (et)\n(el)\nenglish (en)\nfrancais (fr)\ngaeilge (ga)\nhrvatski (hr)\nitaliano (it)\nlatviesu valoda (lv)\nlietuviu kalba (lt)\nmagyar (hu)\nmalti (mt)\'), document(metadata={\'source\': \'https://eur-lex.europa.eu/legal-content/en/txt/?uri=celex:32021l0338\'}, page_content=\'nederlands (nl)\npolski (pl)\nportugues (pt)\nromana (ro)\nslovencina (sk)\nslovenscina (sl)\nsuomi (fi)\nsvenska (sv)\'), document(metadata={\'source\': \'https://eur-lex.europa.eu/legal-content/en/txt/?uri=celex:32021l0338\'}, page_content=\'my eur-lex\nmy eur-lex\nsign

In [31]:
index = pc.Index(index_name)
index.describe_index_stats()

{'dimension': 1536,
 'index_fullness': 0.0,
 'namespaces': {'': {'vector_count': 1271}},
 'total_vector_count': 1271}

In [40]:
# from langchain_pinecone import PineconeVectorStore
# from langchain_openai import OpenAIEmbeddings

# embeddings = OpenAIEmbeddings()
# vectorstore = PineconeVectorStore(index_name=index_name, embedding=embeddings)

In [54]:
vectorstore_from_docs = PineconeVectorStore.from_documents(
        texts,
        index_name=index_name,
        embedding=embeddings
    )

In [55]:
query = "Anti-money laundering in EU."
vectorstore.similarity_search(query)

[Document(metadata={'source': 'https://finance.ec.europa.eu/financial-crime/anti-money-laundering-and-countering-financing-terrorism-eu-level_en#legislation'}, page_content='20 July 2021Legislative proposal - Financial crimeThe European Commission presented an ambitious package of legislative proposals to strengthen the EU’s anti-money laundering and countering the financing of terrorism (AML/CFT) rules. The package harmonises AML/CFT rules across the\xa0EU. It also proposes the creation of a new EU\xa0authority to fight money laundering (AMLA).'),
 Document(metadata={'source': 'https://finance.ec.europa.eu/financial-crime/anti-money-laundering-and-countering-financing-terrorism-eu-level_en#legislation'}, page_content="24 July 2019Communication - Financial crimeThe European Commission adopted a Communication entitled ‘Towards better implementation of the EU's anti-money laundering and countering the financing of terrorism framework’ accompanied by 4\xa0reports.\n\n8 November 2018Opinio

In [56]:
from langchain_openai import ChatOpenAI
from langchain.chains import RetrievalQA
# completion llm
llm = ChatOpenAI(
    openai_api_key=os.getenv("OPENAI_API_KEY"),
    model_name='gpt-3.5-turbo',
    temperature=0.0
)
qa = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",
    retriever=vectorstore.as_retriever()
)
print(qa.run(query))

/home/zeus/miniconda3/envs/cloudspace/lib/python3.10/site-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The method `Chain.run` was deprecated in langchain 0.1.0 and will be removed in 0.3.0. Use invoke instead.
  warn_deprecated(


The European Union has adopted robust legislation to fight against money laundering and terrorist financing (AML). The legislative framework has been constantly revised to mitigate new risks related to money laundering and terrorist financing. This includes harmonizing AML/CFT rules across the EU, proposing the creation of a new EU authority to fight money laundering (AMLA), and covering areas such as virtual assets and crowdfunding. The EU's anti-money laundering directives require obliged entities to apply customer due diligence requirements to prevent the misuse of the financial system for money laundering purposes.


## Healthcare & Data Privacy

#### Wikipedia

In [1]:
from langchain.text_splitter import CharacterTextSplitter
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.docstore.document import Document
from langchain.document_loaders import UnstructuredURLLoader
from langchain.chains.qa_with_sources import load_qa_with_sources_chain
from langchain.vectorstores.pinecone import Pinecone
from langchain.chains import RetrievalQA
from langchain import OpenAI
from langchain_openai import ChatOpenAI
from cleantext import clean
import os
import nltk
import pinecone
import openai
import dotenv

Since the GPL-licensed package `unidecode` is not installed, using Python's `unicodedata` package which yields worse results.


In [2]:
from langchain_community.document_loaders import WikipediaLoader

In [96]:
docs = WikipediaLoader(query="General Data Protection Regulation", doc_content_chars_max = 100000, load_max_docs=1).load()

In [97]:
docs[0].metadata  # meta-information of the Document

{'title': 'General Data Protection Regulation',
 'summary': 'The General Data Protection Regulation (Regulation (EU) 2016/679, abbreviated GDPR) is a European Union regulation on information privacy in the European Union (EU) and the European Economic Area (EEA). The GDPR is an important component of EU privacy law and human rights law, in particular Article 8(1) of the Charter of Fundamental Rights of the European Union. It also governs the transfer of personal data outside the EU and EEA. The GDPR\'s goals are to enhance individuals\' control and rights over their personal information and to simplify the regulations for international business.  It supersedes the Data Protection Directive 95/46/EC and, among other things, simplifies the terminology.\nThe European Parliament and Council of the European Union adopted the GDPR on 14 April 2016, to become effective on 25 May 2018. As an EU regulation (instead of a directive), GDPR is directly applicable with force of law on its own withou

In [98]:
print(docs[0].page_content)

The General Data Protection Regulation (Regulation (EU) 2016/679, abbreviated GDPR) is a European Union regulation on information privacy in the European Union (EU) and the European Economic Area (EEA). The GDPR is an important component of EU privacy law and human rights law, in particular Article 8(1) of the Charter of Fundamental Rights of the European Union. It also governs the transfer of personal data outside the EU and EEA. The GDPR's goals are to enhance individuals' control and rights over their personal information and to simplify the regulations for international business.  It supersedes the Data Protection Directive 95/46/EC and, among other things, simplifies the terminology.
The European Parliament and Council of the European Union adopted the GDPR on 14 April 2016, to become effective on 25 May 2018. As an EU regulation (instead of a directive), GDPR is directly applicable with force of law on its own without the need of transposition. However, it also provides flexibili

In [99]:
documents = []
documents.extend(docs)
print(len(documents))

1


In [100]:
documents

[Document(metadata={'title': 'General Data Protection Regulation', 'summary': 'The General Data Protection Regulation (Regulation (EU) 2016/679, abbreviated GDPR) is a European Union regulation on information privacy in the European Union (EU) and the European Economic Area (EEA). The GDPR is an important component of EU privacy law and human rights law, in particular Article 8(1) of the Charter of Fundamental Rights of the European Union. It also governs the transfer of personal data outside the EU and EEA. The GDPR\'s goals are to enhance individuals\' control and rights over their personal information and to simplify the regulations for international business.  It supersedes the Data Protection Directive 95/46/EC and, among other things, simplifies the terminology.\nThe European Parliament and Council of the European Union adopted the GDPR on 14 April 2016, to become effective on 25 May 2018. As an EU regulation (instead of a directive), GDPR is directly applicable with force of law

In [101]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
texts = text_splitter.split_documents(documents)
texts

[Document(metadata={'title': 'General Data Protection Regulation', 'summary': 'The General Data Protection Regulation (Regulation (EU) 2016/679, abbreviated GDPR) is a European Union regulation on information privacy in the European Union (EU) and the European Economic Area (EEA). The GDPR is an important component of EU privacy law and human rights law, in particular Article 8(1) of the Charter of Fundamental Rights of the European Union. It also governs the transfer of personal data outside the EU and EEA. The GDPR\'s goals are to enhance individuals\' control and rights over their personal information and to simplify the regulations for international business.  It supersedes the Data Protection Directive 95/46/EC and, among other things, simplifies the terminology.\nThe European Parliament and Council of the European Union adopted the GDPR on 14 April 2016, to become effective on 25 May 2018. As an EU regulation (instead of a directive), GDPR is directly applicable with force of law

In [9]:
%cd regulatory_compliance_advisor

/teamspace/studios/this_studio/regulatory_compliance_advisor


/home/zeus/miniconda3/envs/cloudspace/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: using dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [10]:
dotenv.load_dotenv()

True

In [11]:

#Set the pinecone key
from pinecone import Pinecone
#os.environ["PINECONE_API_KEY"] = os.getenv("PINECONE_API_KEY")

api_key = os.getenv("PINECONE_API_KEY")

# configure client
pc = Pinecone(api_key=api_key)

In [72]:
from pinecone import ServerlessSpec

cloud = 'aws'
region = 'us-east-1'

spec = ServerlessSpec(cloud=cloud, region=region)

In [73]:
import time
index_name = "dataprivacy"

In [74]:
# we create a new index
pc.create_index(
        index_name,
        dimension=1536,  # dimensionality of text-embedding-ada-002
        metric='dotproduct',
        spec=spec
    )

In [102]:
index = pc.Index(index_name)
index.describe_index_stats()

{'dimension': 1536,
 'index_fullness': 0.0,
 'namespaces': {'': {'vector_count': 145}},
 'total_vector_count': 145}

In [76]:
from langchain_pinecone import PineconeVectorStore
from langchain_openai import OpenAIEmbeddings

embeddings = OpenAIEmbeddings()
vectorstore = PineconeVectorStore(index_name=index_name, embedding=embeddings)

In [104]:
vectorstore_from_docs = PineconeVectorStore.from_documents(
        texts,
        index_name=index_name,
        embedding=embeddings
    )

PineconeApiException: (400)
Reason: Bad Request
HTTP response headers: HTTPHeaderDict({'Date': 'Mon, 22 Jul 2024 05:56:41 GMT', 'Content-Type': 'application/json', 'Content-Length': '115', 'Connection': 'keep-alive', 'x-pinecone-request-latency-ms': '43', 'x-pinecone-request-id': '6694860687040842690', 'x-envoy-upstream-service-time': '8', 'server': 'envoy'})
HTTP response body: {"code":3,"message":"Metadata size is 50023 bytes, which exceeds the limit of 40960 bytes per vector","details":[]}


In [105]:
query = "What is GDPR?"
vectorstore.similarity_search(query)

[Document(metadata={'source': 'https://www.proofpoint.com/us/threat-reference/ccpa-compliance#:~:text=CCPA%20compliance%20is%20a%20set%20of%20regulations%20that,implement%20reasonable%20security%20measures%20to%20protect%20user%20data'}, page_content='CCPA and GDPR are two data privacy laws that aim to protect the data privacy rights of individuals. Although they share some similarities, there are fundamental differences between them regarding applicability, scope, sensitive personal data, consent, and enforcement.'),
 Document(metadata={'source': 'https://www.proofpoint.com/us/threat-reference/ccpa-compliance#:~:text=CCPA%20compliance%20is%20a%20set%20of%20regulations%20that,implement%20reasonable%20security%20measures%20to%20protect%20user%20data'}, page_content='Enforcement: Supervisory authorities in each EU member state enforce the GDPR, while the California Attorney General’s office enforces the CCPA.\n\nWhile both CCPA and GDPR aim to protect the data privacy rights of individua

In [79]:
from langchain_openai import ChatOpenAI
from langchain.chains import RetrievalQA
# completion llm
llm = ChatOpenAI(
    openai_api_key=os.getenv("OPENAI_API_KEY"),
    model_name='gpt-4o-mini',
    temperature=0.0
)
qa = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",
    retriever=vectorstore.as_retriever()
)
qa.run(query)

"The Children's Online Privacy Protection Act of 1998 (COPPA) is a United States federal law that aims to protect the privacy of children under the age of 13 online. It requires websites and online services directed at children to obtain verifiable parental consent before collecting, using, or disclosing personal information from children. The law addresses concerns about children's online privacy and the necessity of parental consent."

#### URLs

In [87]:
#n_weblinks = int(input("How many web links you want the RAG agent to refer for response generation & insights? Enter here: "))
urls = []
inp = input("Enter Link:")
urls.append(inp)
print("URL:", urls)

URL: ['https://www.proofpoint.com/us/threat-reference/ccpa-compliance#:~:text=CCPA%20compliance%20is%20a%20set%20of%20regulations%20that,implement%20reasonable%20security%20measures%20to%20protect%20user%20data']


In [88]:
loader = UnstructuredURLLoader(urls=urls, show_progress_bar=True)
urls = loader.load()

100%|██████████| 1/1 [00:00<00:00,  1.80it/s]


In [89]:
documents = []
documents.extend(urls)
print(len(documents))

1


In [90]:
print(documents[0].page_content)

Glossary

What Is CCPA Compliance?

What Is CCPA Compliance?

Access the Archiving & Compliance Solution Brief

Start Your Free Trial

Table of Contents

Definition

Who Must Comply With CCPA?

What Does CCPA Cover?

What Are Key Privacy Provisions in CCPA?

What’s the Difference Between CCPA vs. GDPR?

What Is CCPA Compliance Training?

What Are CCPA Penalties for Violating Compliance Requirements?

What Does CCPA Mean for Cybersecurity?

How to Become CCPA Compliant

How Proofpoint Can Help

Definition

The California Consumer Privacy Act (CCPA) was enacted in 2018 to combat the numerous data breaches in Big Tech from poorly defined access controls and privacy management. Modeled after the European Union (EU) General Data Protection Regulation (GDPR), the new regulations give users the right to know when and how their information is being collected and sold, as well as the ability to opt-out.

CCPA compliance is a set of regulations that organizations must follow to protect the data 

In [91]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
texts = text_splitter.split_documents(documents)
texts

[Document(metadata={'source': 'https://www.proofpoint.com/us/threat-reference/ccpa-compliance#:~:text=CCPA%20compliance%20is%20a%20set%20of%20regulations%20that,implement%20reasonable%20security%20measures%20to%20protect%20user%20data'}, page_content='Glossary\n\nWhat Is CCPA Compliance?\n\nWhat Is CCPA Compliance?\n\nAccess the Archiving & Compliance Solution Brief\n\nStart Your Free Trial\n\nTable of Contents\n\nDefinition\n\nWho Must Comply With CCPA?\n\nWhat Does CCPA Cover?\n\nWhat Are Key Privacy Provisions in CCPA?\n\nWhat’s the Difference Between CCPA vs. GDPR?\n\nWhat Is CCPA Compliance Training?\n\nWhat Are CCPA Penalties for Violating Compliance Requirements?\n\nWhat Does CCPA Mean for Cybersecurity?\n\nHow to Become CCPA Compliant\n\nHow Proofpoint Can Help'),
 Document(metadata={'source': 'https://www.proofpoint.com/us/threat-reference/ccpa-compliance#:~:text=CCPA%20compliance%20is%20a%20set%20of%20regulations%20that,implement%20reasonable%20security%20measures%20to%20prot

In [93]:
vectorstore_from_docs = PineconeVectorStore.from_documents(
        texts,
        index_name=index_name,
        embedding=embeddings
    )

In [94]:
query = "What is CCPA?"
vectorstore.similarity_search(query)

[Document(metadata={'source': 'https://en.wikipedia.org/wiki/Children%27s_Online_Privacy_Protection_Act', 'summary': "The Children's Online Privacy Protection Act of 1998 (COPPA) is a United States federal law, located at 15 U.S.C. §§ 6501–6506 (Pub. L.Tooltip Public Law (United States) 105–277 (text) (PDF), 112 Stat. 2681-728, enacted October 21, 1998).\nThe act, effective April 21, 2000, applies to the online collection of personal information by persons or entities under U.S. jurisdiction about children under 13 years of age, including children outside the U.S. if the website or service is U.S.-based. It details what a website operator must include in a privacy policy, when and how to seek verifiable consent from a parent or guardian, and what responsibilities an operator has to protect children's privacy and safety online, including restrictions on the marketing of those under 13.\nAlthough children under 13 can legally give out personal information with their parents' permission, 

In [95]:
from langchain_openai import ChatOpenAI
from langchain.chains import RetrievalQA
# completion llm
llm = ChatOpenAI(
    openai_api_key=os.getenv("OPENAI_API_KEY"),
    model_name='gpt-4o-mini',
    temperature=0.0
)
qa = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",
    retriever=vectorstore.as_retriever()
)
print(qa.run(query))

The California Consumer Privacy Act (CCPA) is a law enacted in 2018 to enhance privacy rights and consumer protection for residents of California. It aims to address data breaches and improve privacy management by giving consumers the right to know what personal information is being collected about them, how it is used and shared, and the ability to opt-out of the sale of their information. The CCPA includes several key provisions that organizations must comply with to protect the data privacy rights of California residents.
